# First pass: waypoint detection

We will pass through all trajectories in order to obtain all the turning points, write them down to a CSV file

<span style="color:red">CAUTION: Do not run all cells in this notebook.</span>

In [1]:
import numpy as np 
from matplotlib import pyplot as plt
import os
from get_turn import load_turnandrise_from_zarr, TurnAndRise
import pandas as pd

In [2]:
# List all files in the '../data/osstate/routes/' directory
date_folders = os.listdir('../data/osstate/routes/')
date_folders.sort()
print('There are {} date folders in the ../data/osstate/routes/ directory'.format(len(date_folders)))

There are 84 date folders in the ../data/osstate/routes/ directory


In [3]:
import random
import string

def generate_random_string(length = 12):
    letters = string.ascii_letters + string.digits
    return ''.join(random.choice(letters) for _ in range(length))

In [ ]:
def process_folder(folder_path: str) -> None:
    
    # List all files in the folder
    files = os.listdir(folder_path)
    files.sort()
    print('There are {} files in the folder {}'.format(len(files), folder_path))
    # Create a CSV file to store waypoints
    csv_file_wp = open(folder_path + '/waypoints.csv', 'w')
    # raise Exception('Waypoint path is: {}'.format(folder_path + '/waypoints.csv'))
    csv_file_wp.write('ident,lat,lon') # to: time over
    
    # Load the data from the files
    for file in files:
        file_path = os.path.join(folder_path, file)
        # if file does not end in .zarr, skip
        if not file_path.endswith('.zarr'):
            continue
        try:
            turn_and_rise:TurnAndRise = load_turnandrise_from_zarr(file_path)
            # Create a CSV file to store the route for each flight
            # print('Route path is: {}'.format(file_path + '_route.csv'))
            print('Processing {}'.format(file_path + '_route.csv'))
            csv_file_route = open(file_path + '_route.csv', 'w')
            csv_file_route.write('ident,to') # to: time over
            for i in range(len(turn_and_rise['tp_lat'])):
                wp_ident = generate_random_string()
                csv_file_wp.write('\n' + wp_ident + ',' + str(turn_and_rise['tp_lat'][i]) + ',' + str(turn_and_rise['tp_lon'][i]))
                csv_file_route.write('\n' + wp_ident + ',' + str(turn_and_rise['tp_time'][i]))
            csv_file_route.close()
        except Exception as e:
            print('Error processing file {}. Skip.'.format(file_path))
            print(e)
            if csv_file_route:
                csv_file_route.close()
            continue 
        
    csv_file_wp.close()

# List all folders in routes
for folder in date_folders:
    print('Processing folder {}'.format(folder))
    process_folder('../data/osstate/routes/' + folder)

# Second pass

Merging the routes of dangling flights

In [5]:
from typing import List

In [6]:
def merge_dangling() -> None: 
    # List all folders in the '../data/osstate/routes/' directory
    date_folders = os.listdir('../data/osstate/routes/')
    date_folders.sort()
    print('date folders: {}'.format(date_folders))
    # date_folders: ['states_2022-01-03-00.csv', 'states_2022-01-03-01.csv',...]
    print('There are {} date folders in the ../data/osstate/routes/ directory'.format(len(date_folders)))
    for folder_no, folder in enumerate(date_folders):
        if folder_no == 0:
            continue # Skip the first folder
        preceding_folder_name = date_folders[folder_no - 1]
        dangling_csv_filename = preceding_folder_name + '.csv' # should be states_2022-01-03-00.csv.csv
        dangling_df = pd.read_csv('../data/osstate/dangling/' + dangling_csv_filename)
        dangling_idents = dangling_df['ident'].unique().tolist()
        
        # List all ZARR subfolders in the folder
        files = os.listdir('../data/osstate/routes/' + folder)
        # files: 'UAE76F_896481.zarr_route.csv', 'UAE76F_896482.zarr', ...
        # Only keep the ZARR subfolders
        zarr_files = [f for f in files if f.endswith('.zarr')]
        zarr_files.sort()
        # zarr_files: 'UAE76F_896481.zarr'...
        # Open the dangling ident instruction csv file
        for zarr_file in zarr_files:
            # Strip the '.zarr' extension
            flight_ident = zarr_file[:-5]
            # Check if the flight_ident is in the dangling_idents
            if flight_ident in dangling_idents:
                # Open the route csv file
                print('Found a dangling ident: {}'.format(flight_ident))
                
                current_route_csv_file = open('../data/osstate/routes/' + folder + '/' + zarr_file + '_route.csv', 'r')
                preceding_route_csv_file = open('../data/osstate/routes/' + preceding_folder_name + '/' + flight_ident + '.zarr_route.csv', 'r')
                
                # print('current_route_csv_file: {}'.format(current_route_csv_file))
                # print('preceding_route_csv_file: {}'.format(preceding_route_csv_file))
                # return
                
                # Copy the whole preceding route csv file to the current route csv file
                preceding_text = preceding_route_csv_file.read() # Read the whole preceding route csv file
                current_text = current_route_csv_file.read() # Read the whole current route csv file
                preceding_route_csv_file.close() # close the file before reopening in write mode
                # Delete the first line of the current_text
                if '\n' in current_text:
                    current_text = current_text[current_text.index('\n') + 1:]
                if len(current_text) > 0:
                    current_text = preceding_text + '\n' + current_text # concatenate the preceding_text and current_text
                else:
                    current_text = preceding_text
                current_route_csv_file = open('../data/osstate/routes/' + folder + '/' + zarr_file + '_route.csv', 'w')
                current_route_csv_file.write(current_text)
                # raise Exception('STOP HERE PLEASE! Verify before proceeding!')
                print('Merge completed for flight {}'.format(flight_ident))
                current_route_csv_file.close()
                preceding_route_csv_file.close()
                
                
            
merge_dangling()
        

date folders: ['states_2022-01-03-00.csv', 'states_2022-01-03-01.csv', 'states_2022-01-03-02.csv', 'states_2022-01-03-03.csv', 'states_2022-01-03-04.csv', 'states_2022-01-03-05.csv', 'states_2022-01-03-06.csv', 'states_2022-01-03-07.csv', 'states_2022-01-03-08.csv', 'states_2022-01-03-09.csv', 'states_2022-01-03-10.csv', 'states_2022-01-03-11.csv', 'states_2022-01-03-12.csv', 'states_2022-01-03-13.csv', 'states_2022-01-03-14.csv', 'states_2022-01-03-15.csv', 'states_2022-01-03-16.csv', 'states_2022-01-03-17.csv', 'states_2022-01-03-18.csv', 'states_2022-01-03-19.csv', 'states_2022-01-03-20.csv', 'states_2022-01-03-21.csv', 'states_2022-01-03-22.csv', 'states_2022-01-03-23.csv', 'states_2022-01-10-00.csv', 'states_2022-01-10-01.csv', 'states_2022-01-10-02.csv', 'states_2022-01-10-03.csv', 'states_2022-01-10-04.csv', 'states_2022-01-10-05.csv', 'states_2022-01-10-06.csv', 'states_2022-01-10-07.csv', 'states_2022-01-10-08.csv', 'states_2022-01-10-09.csv', 'states_2022-01-10-10.csv', 'stat

In [7]:
# Merge all waypoints together
def merge_waypoints() -> None:
    # List all folders in the '../data/osstate/routes/' directory
    date_folders = os.listdir('../data/osstate/routes/')
    date_folders.sort()
    waypoint_master_csv_file = open('../data/osstate/waypoints_master.csv', 'w')
    waypoint_master_csv_file.write('ident,lat,lon')
    print('There are {} date folders in the ../data/osstate/routes/ directory'.format(len(date_folders)))
    for folder_no, folder in enumerate(date_folders):
        print('Processing folder {}'.format(folder))
        # folder: 'states_2022-01-03-00.csv'
        # find the waypoint.csv file inside the folder
        waypoint_csv_file = open('../data/osstate/routes/' + folder + '/waypoints.csv', 'r')
        # read the content of the file
        waypoint_text = waypoint_csv_file.read()
        waypoint_csv_file.close()
        # write the content to the master file
        waypoint_master_csv_file.write(waypoint_text)
    waypoint_master_csv_file.close()
    
merge_waypoints()
    

There are 84 date folders in the ../data/osstate/routes/ directory
Processing folder states_2022-01-03-00.csv
Processing folder states_2022-01-03-01.csv
Processing folder states_2022-01-03-02.csv
Processing folder states_2022-01-03-03.csv
Processing folder states_2022-01-03-04.csv
Processing folder states_2022-01-03-05.csv
Processing folder states_2022-01-03-06.csv
Processing folder states_2022-01-03-07.csv
Processing folder states_2022-01-03-08.csv
Processing folder states_2022-01-03-09.csv
Processing folder states_2022-01-03-10.csv
Processing folder states_2022-01-03-11.csv
Processing folder states_2022-01-03-12.csv
Processing folder states_2022-01-03-13.csv
Processing folder states_2022-01-03-14.csv
Processing folder states_2022-01-03-15.csv
Processing folder states_2022-01-03-16.csv
Processing folder states_2022-01-03-17.csv
Processing folder states_2022-01-03-18.csv
Processing folder states_2022-01-03-19.csv
Processing folder states_2022-01-03-20.csv
Processing folder states_2022-

In [8]:
def fix_waypoint_master_file() -> None:
    waypoint_master_csv_file = open('../data/osstate/waypoints_master.csv', 'r')
    waypoint_master_text = waypoint_master_csv_file.read()
    # Replace 'ident, lat, lon' with ''
    waypoint_master_text = waypoint_master_text.replace('ident,lat,lon', '')
    # if the first line of waypoint_master_text is '\n', remove it
    first_line = waypoint_master_text[:waypoint_master_text.index('\n')]
    if first_line.strip() == '':
        waypoint_master_text = waypoint_master_text[waypoint_master_text.index('\n') + 1:]
        
    # add 'ident, lat, lon' to the first line
    waypoint_master_text = 'ident,lat,lon\n' + waypoint_master_text
    waypoint_master_csv_file.close()
    waypoint_master_csv_file = open('../data/osstate/waypoints_master.csv', 'w')
    waypoint_master_csv_file.write(waypoint_master_text)
    waypoint_master_csv_file.close()
    
fix_waypoint_master_file()

# CAUTION: Delete files

In [ ]:
import os 

def wipe_slate() -> None:
    # List all folders in the '../data/osstate/routes/' directory
    date_folders = os.listdir('../data/osstate/routes/')
    date_folders.sort()
    print('date folders: {}'.format(date_folders))
    # date_folders: ['states_2022-01-03-00.csv', 'states_2022-01-03-01.csv',...]
    print('There are {} date folders in the ../data/osstate/routes/ directory'.format(len(date_folders)))
    for folder_no, folder in enumerate(date_folders):
        # folder: 'states_2022-01-03-00.csv'
        # delete all .zarr_route.csv files in the folder
        files = os.listdir('../data/osstate/routes/' + folder)
        zarr_route_files = [f for f in files if f.endswith('.zarr_route.csv')]
        for zarr_route_file in zarr_route_files:
            os.remove('../data/osstate/routes/' + folder + '/' + zarr_route_file)
        # delete waypoints.csv in the folder
        try:
            os.remove('../data/osstate/routes/' + folder + '/waypoints.csv')
        except:
            print('Error deleting waypoints.csv in folder {}'.format(folder))
            pass

    # delete waypoints_master.csv
    try:
        os.remove('../data/osstate/waypoints_master.csv')
    except:
        print('Error deleting waypoints_master.csv')
        pass

    print('All files have been deleted')

# CAUTION: Uncomment the line below to delete all files
# wipe_slate() 